### Configuration

Choose which scenario's to include in the comparison

In [1]:
scenarios = {
    'S1': {
        'load':         True,
        'reinitialize': True
    },
    'S2': {
        'load':         True,
        'reinitialize': True
    },
    'S3':{
        'load':         True,
        'reinitialize': True
    },
    'S4':{
        'load':         True,
        'reinitialize': True
    }
}

Choose which keys you want to save in the dataframe

In [2]:
regex = [
    # Energies
    'Eprim',
    'Eren',
    'Esto',
    
    'productionSite.Eboi',
    'productionSite.EhpEl',
    'productionSite.Esun',
    'productionSite.Ehp',
    'productionSite.ECHP',
    'productionSite.EelCHP',
    'productionSite.Esto',
    
    'grid.Egrid',
    'grid.Edis',
    'grid.Ehea',
    'grid.Esh',
    'grid.Edhw',
    'grid.EboosEl',
    'grid.Esto'
    
    # Powers
    'Pprim', 
    'Pren',
    'Qsto',
    
    'productionSite.Pboi',
    'productionSite.PhpEl',
    'productionSite.Qsun',
    'productionSite.Qhp',
    'productionSite.PCHP',
    'productionSite.PelCHP',
    'productionSite.Qsto',
    'productionSite.Qren',
    
    'grid.Qgrid',
    'grid.Qdis',
    'grid.Qhea',
    'grid.Qsh',
    'grid.Qdhw',
    'grid.Qhp',
    'grid.PboosEl',
    'grid.Qsto'
    
    ## Heatingsystems
    '.*TZones',
    '.*TZonem',
    '.*TZoned.*(?<!\))$',
    
    '.*TDhws',
    '.*TDhwm',
    '.*TDhwd.*(?<!\))$',
    
    '.*TSupplym',
    '.*TSupplys'
    
    '.*TGridi',
    '.*TGrido',

    '.*mRad',
    '.*mDhw',
    '.*mDhwReq',
    '.*mSupply',
    
    '.*tan.*vol.*T',
    
    # Grid
    '.*Pipe.*QLosses',
    '.*Pipe.*T.Out',
    
    
    # Production site
    '.*COP$',
    '.*modulation$',
    '.*mGrid$',
    'productionSite.Tret.T'
    
    ## Solar collector parameters
    'productionSite.solar.m_flow',
    'productionSite.TSun.*T',
    'productionSite.bufferSolar.*tan.*vol.*T',
    
    ## Boiler parameters
    'productionSite.boiler.m_flow',
    'productionSite.TBoi.*T',
    
    ## CHP parameters
    'productionSite.cHP.m_flow',
    'productionSite.cHP.Qheating',
    
    ## HP parameters
    'productionSite.hp.m_flow',
    'productionSite.*THp.*T',
    'productionSite.bufferHp.*tan.*vol.*T',
    
]

cumul = [
    'Eprim',
    'Eren',
    'Esto',
    'productionSite.Eboi',
    'productionSite.EhpEl',
    'productionSite.Esun',
    'productionSite.Ehp',
    'productionSite.EChpGas',
    'productionSite.EchpEl',
    'productionSite.Esto',
    'grid.Egrid',
    'grid.Edis',
    'grid.Ehea',
    'grid.Esh',
    'grid.Edhw',
    'grid.EboosEl',
    'grid.Esto'
]

Set the result file location

In [3]:
path = r'M:/De schipjes/Scenarios/'
name = r'year'

### Imports

In [4]:
import os
import sys
import math
import re

import pandas as pd
import numpy as np

from datetime import date
from result import Result, Results, load
from IPython.display import HTML

In [5]:
import charts
charts.default_settings.update(dict(show='tab', stock=True))

Server running in the folder c:\Users\u0098668\Documents\Modelica\DeSchipjes\Notebooks\Analysis at 127.0.0.1:58122


### Initialization

In [6]:
path = os.path.join(path, name)

In [7]:
periods = {
    '1': [[604800, 31556926]],
    '2': [[604800, 15778463], [15778463, 31556926]],
    '3': [[604800, 10518976], [10518976, 21037951], [21037951, 31556926]]
}

In [8]:
def find_keys(regex, result):
    keys = []
    if type(regex) is not list:
        regex = [regex]
    
    for r in regex:
        for k in result.keys:
            if re.match(r, k):
                keys.append(k)
    return list(set(keys))

In [9]:
def load_result(scenario):
    # Find the files with their full path and load the results
    files = filter(lambda x: x.endswith('.mat'), 
        [os.path.join(path, scenario, f) for f in sorted(os.listdir(os.path.join(path, scenario)))])
    return [Result(f) for f in files]

def concat(results, regex):   
    # Get the number of files and calculate the start and stop times 
    n = len(results)
    period = math.ceil(31556926./3)
    
    durations = periods[str(n)]
    
    keys = find_keys(regex, results[0])
    
    # Load the dataframes
    dfs = [r.get(keys) for r in results]
    
    # Slice the correct times
    dfs = [dfs[i].truncate(
        before=date.fromtimestamp(durations[i][0]), 
        after=date.fromtimestamp(durations[i][1])) for i in range(0, n)]
    
    # Cumulate the results if necessary
    for i in range(1, n):
        for k in keys:
            if k in cumul:
                dfs[i][k] = dfs[i][k] + dfs[i-1][k][-1]
                
    # Concat the dataframes and save it
    return pd.concat(dfs) 

def load_df(scenario):
    return load(os.path.join(path, scenario, scenario + '.hdf'))

def save_df(df, scenario):
    dest = os.path.join(path, scenario, scenario + '.hdf')
    df.to_hdf(dest, 'data')

In [10]:
data = dict()
results = dict()
for scenario, config in scenarios.iteritems():
    if config['load']:
        if config['reinitialize']:
            results[scenario] = load_result(scenario)
            data[scenario] = concat(results[scenario], regex)
            save_df(data[scenario], scenario)
        else:
            data[scenario] = load_df(scenario)

Some further data manipulations...

In [42]:
loaded_scenarios = []
for k, v in scenarios.iteritems():
    if v['load']:
        loaded_scenarios.append(k)
        
loaded_scenarios = sorted(loaded_scenarios)

if 'S1' in data:
    data['S1']['Eprim'] = data['S1']['Eprim'] + data['S1']['productionSite.ECHP']
    
placeholder = [
    'productionSite.PElChp',
    'productionSite.QCHP',
    'productionSite.PCHP',
    'productionSite.bufferSolar',
    'productionSite.bufferHp',
    'productionSite.bufferChp'
]
    
for s in loaded_scenarios:
    for p in placeholder:
        if p not in data[s]:
            data[s][p] = 0

loads = {
    'productionSite.boiler': 'Qboi',
    'productionSite.bufferSolar': 'QbufferSolar',
    'productionSite.bufferHp': 'QbufferHp',
    'productionSite.bufferChp': 'QbufferChp',
    'productionSite.cHP': 'QCHP'
}        

In [14]:
months = []
for i in range(1,12):
    months.append([date(1970, i, 1), date(1970, i+1, 1)])

In [15]:
def monthly_diff(df, key, year=True):
    res = []
    
    dates = months[:]
    
    if year:
        dates.append([date(1970, 1, 1), date(1970, 12, 1)])
    
    for m in dates:
        [i1, i2] = [df.index.searchsorted(m[0]), df.index.searchsorted(m[1])]
        [ix1, ix2] = [df.ix[df.index[i1]], df.ix[df.index[i2]]]
    
        res.append(ix2[key]-ix1[key])
        
    return res

def monthly_average(df, key):
    res = []
    
    for m in months:
        tdf = df.truncate(before=m[0], after=m[1])
        res.append(tdf[key].mean())
        
    return res

### Plots

### Total  Energy consumption / production

In [16]:
def value_or_zero(data, s, y, i):
    try:
        return data[s][y][i]
    except KeyError:
        return 0

categories = [
    'Eprim',
    'Eren',
    'Esun',
    'productionSite.Eboi',
    'productionSite.EhpEl',
    'productionSite.Esun',
    'productionSite.Ehp',
    'productionSite.ECHP',
    'productionSite.EelCHP',
    'productionSite.Esto'
]

options = {
    'chart': {'zoomType': 'xy'},
    'title': {'text': 'Total energy consumption and production'},
    'xAxis': {
        'categories': categories
    },
    'yAxis': {'min': 0}
}

series = map(lambda s: {
    'name': s,
    'data': map(lambda y: value_or_zero(data, s, y, -1), categories)
}, loaded_scenarios)

charts.plot(
    type='column', 
    series=series, 
    options=options,
    stock=False,
    show='inline', 
    save=os.path.join(path, options['title']['text']) + '.html')

###Total heat usage

In [17]:
categories = [
    'grid.Egrid',
    'grid.Edis',
    'grid.Ehea',
    'grid.Esh',
    'grid.Edhw',
    'grid.Esto',
    'grid.EboosEl'
]

options = {
    'chart': {'zoomType': 'xy'},
    'title': {'text': 'Heat usage in the grid'},
    'xAxis': {
        'categories': categories
    },
    'yAxis': {'min': 0}
}

series = map(lambda s: {
    'name': s,
    'data': map(lambda y: value_or_zero(data, s, y, -1), categories)
}, loaded_scenarios)

charts.plot(
    type='column', 
    series=series, 
    options=options,
    stock=False,
    show='inline', 
    save=os.path.join(path, options['title']['text']) + '.html')

###Distribution losses

In [18]:
losses = dict(zip(
    loaded_scenarios, 
    map(lambda x: np.array(monthly_diff(data[x], 'grid.Edis')) / np.array(monthly_diff(data[x], 'grid.Egrid'))*100, 
        loaded_scenarios)))

categories = [
    'januari', 
    'februari', 
    'maart', 
    'april', 
    'juni', 
    'juli',
    'augustus', 
    'september', 
    'oktober', 
    'november', 
    'december', 
    'year'
]
options = {
    'chart': {'zoomType': 'xy'},
    'title': {'text': 'Relative distribution losses throughout the year'},
    'xAxis': {
        'categories': categories
    },
    'yAxis': {
        'min': 0,
        'title': {'text': 'Distribution losses [%]'}
    }
}

series = map(lambda x: {
    'name': x,
    'data': losses[x]
}, loaded_scenarios)

charts.plot(
    type='column', 
    series=series, 
    options=options,
    stock=False,
    show='inline', 
    save=os.path.join(path, options['title']['text']) + '.html')

Possible explanations:
 - Losses are **not very dependent** of massflow. The higher the massflow, the more energy is distributed and the smaller the relative losses will be
 - S4 has the lowest energy needed due to the separate DHW production

###Load duration curves for the production site

In [19]:
def ldc(scenario, keys, rule='15T', how='mean'):
    
    sort = 'grid.Qgrid'
    df = data[scenario].resample(rule, how).dropna()
    
    index = df.index.asi8/1e6
    
    sdf = df.sort(sort, ascending=False)[keys]
    sdf.index = index
    
    return sdf

####Comparison of the scenarios

In [20]:
series = []

for s in loaded_scenarios:

    key = 'grid.Qhea'
    
    df = data[s].resample('H', 'max').dropna()
    index = df.index.asi8/1e6
    sdf = df[[key]].sort(key, ascending=False)

    values = sdf[key].values

    series.append({
        'name': s,
        'data': np.array([index, values]).T
    })

options = {
    'legend': {'enabled': True},
    'title': {'text': 'Load duration curve of the Grid heat consumption'},
    'yAxis': {'title': {'text': 'W'}},
    'height': 500
}
    
charts.plot(
    series, 
    options=options, 
    type='line', 
    show='inline'
)

In [60]:
scs = ['S2', 'S3', 'S4']

key = 'grid.Qgrid'
minValue = 0e3

series = []

for s in set(loaded_scenarios).intersection(scs):
    df = data[s][[key]]
    load = df[df[key] > minValue]
    
    index = load.index.asi8/1e6
    values = load[key].values
    
    series.append({
        'name': s,
        'data': np.array([index, values]).T
    })
    
charts.plot(
    series, 
    options=options, 
    type='line', 
    show='tab'
)

Opening new tab...


####Breakdown of where the load is distributed to

In [49]:
keys = [
    'grid.Qsh', 
    'grid.Qdhw',
    'grid.Qdis',
    'productionSite.Qsto'
]

html = []

for s in loaded_scenarios:
    df = ldc(s, keys, rule='H', how='max')

    options = {
        'legend': {'enabled': True},
        'plotOptions': {
            'area': {
                'stacking': 'normal'
            }
        },
        'title': {'text': 'LDC of the consumption'},
        'subtitle': {'text': 'Scenario {0}'.format(s[-1])},
        'height': 600
    }

    html.append(charts.plot(
        df,
        options=options, 
        type='area', 
        save='ldc-cons-' + s + '.html', 
        show='string'))
    
html = ''.join(html)

In [50]:
HTML(html)

####Breakdown of what is producing the load

In [46]:
keys = [
    'productionSite.Pboi',
    'productionSite.Qhp',
    'productionSite.Qsun',
    #'productionSite.PCHP'
]

html = []

for s in loaded_scenarios:
    df = ldc(s, keys, rule='H', how='max')

    options = {
        'legend': {'enabled': True},
        'plotOptions': {
            'area': {
                'stacking': 'normal'
            }
        },
        'title': {'text': 'LDC of the production units'},
        'subtitle': {'text': 'Scenario {0}'.format(s[-1])},
        'height': 600
    }

    html.append(
        charts.plot(
            df, 
            options=options, 
            type='area', 
            save='ldc-prod-' + s + '.html', 
            show='string'))
    
HTML(''.join(html))

In [66]:
df = data['S3'][['productionSite.boiler.m_flow']]

In [67]:
charts.plot(df)

Opening new tab...


In [71]:
for c in data['S3'].columns:
    print c

Eprim
Eren
Esto
grid.EboosEl
grid.Edhw
grid.Edis
grid.Egrid
grid.Ehea
grid.Esh
grid.PboosEl
grid.Pipe1.QLosses
grid.Pipe1.districtHeatingPipe.QLosses
grid.Pipe1.districtHeatingPipe.plugFlowHeatLossTwinPipe.twinExponentialDecay.T1Out
grid.Pipe1.districtHeatingPipe.plugFlowHeatLossTwinPipe.twinExponentialDecay.T2Out
grid.Pipe10.QLosses
grid.Pipe10.districtHeatingPipe.QLosses
grid.Pipe10.districtHeatingPipe.plugFlowHeatLossTwinPipe.twinExponentialDecay.T1Out
grid.Pipe10.districtHeatingPipe.plugFlowHeatLossTwinPipe.twinExponentialDecay.T2Out
grid.Pipe11.QLosses
grid.Pipe11.districtHeatingPipe.QLosses
grid.Pipe11.districtHeatingPipe.plugFlowHeatLossTwinPipe.twinExponentialDecay.T1Out
grid.Pipe11.districtHeatingPipe.plugFlowHeatLossTwinPipe.twinExponentialDecay.T2Out
grid.Pipe2.QLosses
grid.Pipe2.districtHeatingPipe.QLosses
grid.Pipe2.districtHeatingPipe.plugFlowHeatLossTwinPipe.twinExponentialDecay.T1Out
grid.Pipe2.districtHeatingPipe.plugFlowHeatLossTwinPipe.twinExponentialDecay.T2Out
grid